In [1]:
import sys
sys.path.append('../')
import argparse
import os
import torch
import time
import torch.nn as nn
import numpy as np
from dataloader import * 
import cv2
import matplotlib.pyplot as plt
from torchvision import transforms
from utils.utils import *
from tqdm import tqdm
from scipy import spatial
from scipy.io import wavfile
import librosa
from vggm import VGGM
from resnet import *
from senet import *
import traceback
from facenet_pytorch import InceptionResnetV1
from facenet_pytorch import MTCNN
from signal_utils import preprocess
import warnings
warnings.filterwarnings('ignore')

In [2]:
class AudioInference():
    def __init__(self):
        self.device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
        print(self.device)

        # self.model=VGGM(1251)
        # # self.model.load_state_dict(torch.load("../VGGVox-PyTorch-master/models/VGGM300_BEST_140_81.99.pth", map_location=device))
        # self.model.load_state_dict(torch.load("/home/starc52/audret/models/VGGM300_BEST_140_81.99.pth", map_location=self.device))
        # self.model.to(self.device)
        # print("VggVox model loaded")
        # self.model.eval()
        # self.preprocess = preprocess(arch_type=arch_type)
        

    def get_audio_features(self, audio_path, save_path=None, img=None):

        audio,sr=librosa.load(audio_path,sr=16000)

        audio = audio[0:48000]

        audio = preprocess(audio).astype(np.float32)
        audio=np.expand_dims(audio, 2)

        transformers=transforms.ToTensor()
        audio = transformers(audio)
        audio = audio.unsqueeze(0)

        audio = audio.to(self.device)

        with torch.no_grad():
            audio_embedding = self.model(audio)

        audio_embedding = audio_embedding.cpu().numpy()
    
        return audio_embedding

    # todo
    #takes audio as input, splits it with window and stride params, then comptues the embeddings
    def split_audio(self, audio, window=3, stride=2, sr=16000) :
        # window and stride is in seconds

        if type(audio)==str:
            pathToAudio = audio
            audio,sr=librosa.load(audio,sr=16000)

        nsamples_per_window = int(window*sr)
        samples_per_stride = int(stride*sr)

        slice_start = [i for i in range(0,len(audio)-nsamples_per_window,samples_per_stride)]
        slice_end = [i+nsamples_per_window if i+nsamples_per_window<len(audio) else len(audio) for i in slice_start]
               
        audios = [audio[slice_start[i]:slice_end[i]] for i in range(len(slice_start))]
        if audios:
            audios = random.sample(audios, 1)
        else:
            print("No audios available")
            return []
        audios_processed = [preprocess(audio).astype(np.float32) for audio in audios]
        audios_expanded = [np.expand_dims(audio, 2) for audio in audios_processed]
        try:
            os.makedirs(pathToAudio[:-4])
            [np.save(join(pathToAudio[:-4], "%03d.npy"%idx), audio_fft) for idx, audio_fft in enumerate(audios_expanded)]
            return audios_expanded
        except:
            print("audio_fft directory already present")
        # transformers = transforms.ToTensor()
        # audios_transformed = [transformers(audio) for audio in audios_expanded]
        # audios_unsqzd = [audio.unsqueeze(0) for audio in audios_transformed]
        # embeddings = []
        # try:
        #     os.makedirs(pathToAudio[:-4])
        #     for idx, audio in enumerate(audios_unsqzd):
        #         audio_temp = audio.to(self.device)
        #         with torch.no_grad():
        #             audio_embedding = self.model(audio_temp)
        #         audio_embedding = audio_embedding.cpu().numpy()
        #         np.save(join(pathToAudio[:-4], "%03d.npy"%idx), audio_embedding)
        #         embeddings.append(audio_embedding)
        # except:
        #     print("directory present")
        
        # return embeddings

In [3]:
# parser = argparse.ArgumentParser()
# parser.add_argument('--root',default='/scratch/starc52/VoxCeleb2/dev/mp4', type=str)
# parser.add_argument('--model_val_path',default="/home/starc52/Recode/senet.pth", type=str)
# parser.add_argument('--start_id', default=0, type=int)
# parser.add_argument('--end_id', default=5994, type=int)
# args = parser.parse_args()
root = '/scratch/starc52/VoxCeleb2/test/mp4'
model_val_path = "/home/starc52/Recode/senet.pth"
start_id = 0
end_id = 999

# print(args)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
mtcnn = MTCNN(post_process=False, keep_all=True, device=device)
AudioModel = AudioInference()

criterion_kldiv = nn.KLDivLoss()
criterion_mse = nn.MSELoss()
criterion_cosine = nn.CosineSimilarity()

kldiv_loss = AverageMeter()
mse_loss = AverageMeter()
cosine_loss = AverageMeter()
listOfIdentities=sorted(os.listdir(root))[start_id:end_id]
for speaker_id in tqdm(sorted(os.listdir(root))[start_id:end_id]):#just 1000 user ids. 
    for url in sorted(os.listdir(join(root, speaker_id))):
        # os.makedirs(join(save_path, speaker_id, url), exist_ok=True)
        for file_name in sorted(os.listdir(join(root, speaker_id, url))):
            try:
                if file_name[-4:] == ".mp4":
                    cap = cv2.VideoCapture(join(root, speaker_id, url, file_name))
                    transformToTensor = transforms.ToTensor()
                    ret, img_file=cap.read()
                    if img_file is not None:
                        print(type(img_file))
                        faces = mtcnn(img_file)
                    else:
                        continue
                    if faces is None:
                        count=0
                        while cap.isOpened():
                            ret, frame = cap.read()
                    
                            img_file=np.array(frame, copy=True)
                            if not ret:
                                break
                            faces = mtcnn(img_file)
                            if ret and faces is not None:
                                cap.release()
                                break
                            count+=1
                            cap.set(1, count)
                    if faces is None:
                        print("No face detected for : %s" % join(root, speaker_id, url, file_name))
                        os.remove(join(root, speaker_id, url, file_name))
                        continue
                    img_file = faces[0]
                    img_file = img_file.permute(1, 2, 0).numpy()
                    img_file  = cv2.resize(img_file, (224, 224))
                    cv2.imwrite(join(root, speaker_id, url, file_name[:-4]+".jpg"), img_file)
                    os.remove(join(root, speaker_id, url, file_name))
                    print("Processed filename: %s"% join(root, speaker_id, url, file_name))

                elif file_name[-4:] == ".wav":
                        utteranceEmbedding = AudioModel.split_audio(join(root, speaker_id, url, file_name))
                        os.remove(join(root, speaker_id, url, file_name))
                        print("Processed filename: %s"% join(root, speaker_id, url, file_name))
            except:
                print("%tb"%traceback.format_exc())
                continue
print(listOfIdentities)


cuda


  0%|          | 0/118 [00:00<?, ?it/s]

<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/01dfn2spqyE/00001.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/01dfn2spqyE/00001.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/5MkXgwdrmJw/00002.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/5MkXgwdrmJw/00002.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/7t6lfzvVaTM/00003.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/7t6lfzvVaTM/00003.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/7t6lfzvVaTM/00004.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/7t6lfzvVaTM/00004.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/7t6lfzvVaTM/00005.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/7t6lfzvVaTM/00005.wav
<class 'numpy.ndarra

<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00046.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00046.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00047.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00047.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00048.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00048.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00049.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00049.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00050.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/OLguY5ofUrY/00050.wav
<class 'numpy.ndarra

Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00107.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00107.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00108.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00108.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00109.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00109.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00110.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00110.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00111.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id00017/gjYcaCzo7UU/00111.wav
<class 'numpy.ndarray'>
Processed filename: 

...

<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/oF8cALd6lU0/00271.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/oF8cALd6lU0/00271.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00272.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00272.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00273.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00273.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00274.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00274.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00275.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/p8b5sqw96dQ/00275.wav
<class 'numpy.ndarra

<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00314.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00314.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00315.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00315.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00316.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00316.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00317.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00317.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00318.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/vnd8dfg_x5Y/00318.wav
<class 'numpy.ndarra

<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zIK2nqL4VkY/00359.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zIK2nqL4VkY/00359.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zIK2nqL4VkY/00360.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zIK2nqL4VkY/00360.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zIK2nqL4VkY/00361.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zIK2nqL4VkY/00361.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zXNFMbxS2oc/00362.mp4


100%|██████████| 118/118 [51:56<00:00, 26.41s/it]

Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zXNFMbxS2oc/00362.wav
<class 'numpy.ndarray'>
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zXNFMbxS2oc/00363.mp4
Processed filename: /scratch/starc52/VoxCeleb2/test/mp4/id09017/zXNFMbxS2oc/00363.wav
['id00017', 'id00061', 'id00081', 'id00154', 'id00419', 'id00562', 'id00812', 'id00817', 'id00866', 'id00926', 'id01000', 'id01041', 'id01066', 'id01106', 'id01224', 'id01228', 'id01298', 'id01333', 'id01437', 'id01460', 'id01509', 'id01541', 'id01567', 'id01593', 'id01618', 'id01822', 'id01892', 'id01989', 'id02019', 'id02057', 'id02086', 'id02181', 'id02286', 'id02317', 'id02445', 'id02465', 'id02542', 'id02548', 'id02576', 'id02577', 'id02685', 'id02725', 'id02745', 'id03030', 'id03041', 'id03127', 'id03178', 'id03347', 'id03382', 'id03524', 'id03677', 'id03789', 'id03839', 'id03862', 'id03969', 'id03978', 'id03980', 'id03981', 'id04006', 'id04030', 'id04094', 'id04119', 'id04232', 'id04253', 'id04276', 'i